In [5]:
#Mounting drive
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [6]:
from google.colab import files
uploaded = files.upload()

Saving requirements.txt to requirements.txt


In [7]:
!pip install -r requirements.txt


In [8]:
!pip install ultralytics

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 645.2/645.2 kB 5.4 MB/s eta 0:00:00


In [9]:
from ultralytics import YOLO
import cv2
from pathlib import Path
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import os
from types import SimpleNamespace
import time
from sklearn.model_selection import train_test_split
from zipfile import ZipFile
import shutil

In [ ]:
zip_file_path = '/content/drive/Shareddrives/Nikhil shared drive/COCO-Hand.zip'
extraction_path = '/content/data/'

In [ ]:
# Unzip the file
with ZipFile(zip_file_path, 'r') as zip_ref:
    zip_ref.extractall(extraction_path)

print("Unzipped successfully!")

Unzipped successfully!


In [ ]:
#Splitting the dataset into train,test and val sets
def split_images(images_dir, output_dir):
    """
    Splits images into train, val, and test sets and move them to respective folders.
    """

    # List all image filenames
    images = [f for f in os.listdir(images_dir) if f.endswith('.jpg')]

    # Split the filenames into train, val, and test sets
    train_images, temp_images = train_test_split(images, test_size=0.2, random_state=42)
    val_images, test_images = train_test_split(temp_images, test_size=0.5, random_state=42)

    # Dictionaries to map split name to filenames
    splits = {
        'train': train_images,
        'val': val_images,
        'test': test_images
    }

    # Create directories for each split and move images to them
    for split, split_images in splits.items():
        split_dir = Path(output_dir) / split / 'images'
        split_dir.mkdir(parents=True, exist_ok=True)
        for img in split_images:
            shutil.move(images_dir / img, split_dir / img)

    return splits

# Test the function
images_dir = Path("/content/data/COCO-Hand/COCO-Hand-Big/COCO-Hand-Big_Images")
output_dir = Path("/content/data/COCO-Hand/COCO-Hand-Big")

# Call the function to split images
splits = split_images(images_dir, output_dir)



In [ ]:
def load_annotations_from_file(annotation_file_path):
    """
    Load annotations from the specified file.
    """
    with open(annotation_file_path, 'r') as file:
        annotations = [line.strip().split() for line in file.readlines()]
    return annotations

annotations = load_annotations_from_file('/content/data/COCO-Hand/COCO-Hand-Big/COCO-Hand-Big_annotations.txt')
print(f"Total annotations loaded: {len(annotations)}")

Total annotations loaded: 50669


In [ ]:
# Define paths for each split
train_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/train/images"
train_labels_path = "/content/data/COCO-Hand/COCO-Hand-Big/train/labels"
val_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/val/images"
val_labels_path = "/content/data/COCO-Hand/COCO-Hand-Big/val/labels"
test_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/test/images"
test_labels_path = "/content/data/COCO-Hand/COCO-Hand-Big/test/labels"


In [ ]:
#path for the annotations file
annotations_file_path = "/content/data/COCO-Hand/COCO-Hand-Big/COCO-Hand-Big_annotations.txt"



# Load annotations from the provided file
with open(annotations_file_path, 'r') as file:
    annotations_data = [line.strip() for line in file.readlines()]


# Define paths for each set
train_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/train/images"
val_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/val/images"
test_images_path = "/content/data/COCO-Hand/COCO-Hand-Big/test/images"


# Get image filenames from each directory and combine them
train_image_filenames = [f for f in os.listdir(train_images_path) if f.endswith('.jpg')]
val_image_filenames = [f for f in os.listdir(val_images_path) if f.endswith('.jpg')]
test_image_filenames = [f for f in os.listdir(test_images_path) if f.endswith('.jpg')]


test_relevant_annotations = [ann for ann in annotations_data if any(img in ann for img in test_image_filenames)]
train_relevant_annotations = [ann for ann in annotations_data if any(img in ann for img in train_image_filenames)]

val_relevant_annotations = [ann for ann in annotations_data if any(img in ann for img in val_image_filenames)]

print(train_relevant_annotations)
print(len(train_relevant_annotations))


['000000000077.jpg,29,47,254,276,47,259,38,254,29,272,38,276,hand', '000000000077.jpg,291,307,58,69,291,62,294,69,307,65,305,58,hand', '000000000077.jpg,292,305,58,69,292,63,295,69,305,64,302,58,hand', '000000000077.jpg,307,315,76,86,315,78,311,76,307,85,311,86,hand', '000000000322.jpg,189,212,148,167,194,148,189,157,208,167,212,158,hand', '000000000322.jpg,53,75,163,186,75,171,65,163,53,178,63,186,hand', '000000000389.jpg,426,446,246,264,440,264,446,255,432,246,426,255,hand', '000000000431.jpg,218,231,148,159,219,148,218,156,230,159,231,151,hand', '000000000436.jpg,98,246,89,173,98,151,164,173,246,111,180,89,hand', '000000000436.jpg,265,444,149,225,404,225,444,181,305,149,265,193,hand', '000000000510.jpg,223,252,179,211,223,179,223,211,252,211,251,179,hand', '000000000510.jpg,228,268,180,209,267,209,268,181,228,180,228,208,hand', '000000000532.jpg,206,214,233,245,211,233,206,234,209,245,214,243,hand', '000000000532.jpg,228,233,224,232,233,224,228,224,228,232,233,232,hand', '0000000005

In [ ]:
from PIL import Image

def convert_to_yolo_format(annotation, image_path):
    """
    Convert COCO-Hand annotation to YOLO format.
    """
    # Extract bounding box coordinates
    parts = annotation.split(',')
    image_name = parts[0]
    xmin, xmax, ymin, ymax = map(float, parts[1:5])

    # Calculate absolute width and height
    width_abs = abs(xmax - xmin)
    height_abs = abs(ymax - ymin)

    # Load the image to get its width and height
    with Image.open(image_path) as img:
        img_width, img_height = img.size

    # Calculate YOLO format values
    x_center = ((xmin + xmax) / 2) / img_width
    y_center = ((ymin + ymax) / 2) / img_height
    width = width_abs / img_width
    height = height_abs / img_height

    return [0, x_center, y_center, width, height]  # 0 is the class_id for 'hand'



In [ ]:

# Creating a dictionary to store annotations for each image for TEST dataset
print(test_relevant_annotations)
test_annotations_dict = {}
for ann in test_relevant_annotations:
    image_name = ann.split(',')[0]
    if image_name not in test_annotations_dict:
        test_annotations_dict[image_name] = []
    test_annotations_dict[image_name].append(ann)
print(test_annotations_dict)

['000000000446.jpg,280,361,192,228,296,192,280,212,346,228,361,207,hand', '000000000446.jpg,283,345,198,219,284,198,283,218,343,219,345,199,hand', '000000001145.jpg,148,198,185,224,148,201,157,224,198,208,189,185,hand', '000000001145.jpg,157,192,171,201,166,171,157,183,184,201,192,188,hand', '000000001232.jpg,287,293,205,214,288,214,293,213,292,205,287,205,hand', '000000001403.jpg,50,176,304,391,176,356,159,304,50,338,67,391,hand', '000000001407.jpg,249,281,111,129,249,126,275,129,281,114,255,111,hand', '000000001431.jpg,392,396,120,128,396,120,392,120,392,128,396,128,hand', '000000001431.jpg,419,428,118,132,428,119,423,118,419,130,424,132,hand', '000000001431.jpg,161,185,17,34,184,34,185,19,163,17,161,33,hand', '000000001431.jpg,347,366,77,110,347,110,366,110,366,77,347,77,hand', '000000001431.jpg,112,127,154,175,127,157,119,154,112,172,120,175,hand', '000000001431.jpg,56,71,158,186,71,161,62,158,56,183,66,186,hand', '000000001431.jpg,249,265,64,87,265,68,255,64,249,84,259,87,hand', '

In [ ]:
#Create a dictionary to store annotations for each image for train dataset
train_annotations_dict = {}
for ann in train_relevant_annotations:
    image_name = ann.split(',')[0]
    if image_name not in train_annotations_dict:
        train_annotations_dict[image_name] = []
    train_annotations_dict[image_name].append(ann)
print(len(train_annotations_dict))

21199


In [ ]:
#Create a dictionary to store annotations for each image for val dataset
val_annotations_dict = {}
for ann in val_relevant_annotations:
    image_name = ann.split(',')[0]
    if image_name not in val_annotations_dict:
        val_annotations_dict[image_name] = []
    val_annotations_dict[image_name].append(ann)
print(val_annotations_dict)

{'000000000036.jpg': ['000000000036.jpg,216,257,208,257,230,257,257,255,243,208,216,211,hand', '000000000036.jpg,419,469,339,386,449,339,419,343,439,386,469,381,hand'], '000000000165.jpg': ['000000000165.jpg,109,182,210,253,109,224,116,253,182,239,174,210,hand', '000000000165.jpg,219,274,262,312,243,262,219,280,250,312,274,294,hand', '000000000165.jpg,185,237,217,257,226,257,237,229,195,217,185,245,hand', '000000000165.jpg,244,298,170,202,293,202,298,177,249,170,244,195,hand'], '000000000735.jpg': ['000000000735.jpg,233,261,178,224,244,178,233,188,249,224,261,215,hand', '000000000735.jpg,272,291,167,191,277,167,272,183,287,191,291,176,hand'], '000000000897.jpg': ['000000000897.jpg,325,354,279,312,350,279,325,283,329,312,354,307,hand'], '000000001107.jpg': ['000000001107.jpg,255,265,330,343,260,330,255,334,259,343,265,339,hand', '000000001107.jpg,229,237,329,339,237,330,230,329,229,338,236,339,hand'], '000000001381.jpg': ['000000001381.jpg,302,319,204,221,319,208,306,204,302,217,315,221

In [ ]:
# Convert each annotation to YOLO format and save to .txt file for TEST IMAGES
for image_name, image_annotations in test_annotations_dict.items():
    yolo_formatted_annotations = [convert_to_yolo_format(ann, os.path.join(test_images_path, image_name)) for ann in image_annotations]  # Use image_annotations instead of test_relevant_annotations
    yolo_strings = [" ".join(map(str, ann)) for ann in yolo_formatted_annotations]

    txt_path = os.path.join(test_labels_path, image_name.replace('.jpg', '.txt'))

    labels_directory = os.path.dirname(txt_path)
    if not os.path.exists(labels_directory):
      os.makedirs(labels_directory)

    with open(txt_path, 'w') as f:
        f.write("\n".join(yolo_strings))


In [ ]:

# Convert each annotation to YOLO format and save to .txt file FOR TRAIN IMAGES
for image_name, image_annotations in train_annotations_dict.items():
    yolo_formatted_annotations = [convert_to_yolo_format(ann, os.path.join(train_images_path, image_name)) for ann in image_annotations]
    yolo_strings = [" ".join(map(str, ann)) for ann in yolo_formatted_annotations]

    txt_path = os.path.join(train_labels_path, image_name.replace('.jpg', '.txt'))

    labels_directory = os.path.dirname(txt_path)
    if not os.path.exists(labels_directory):
      os.makedirs(labels_directory)

    with open(txt_path, 'w') as f:
        f.write("\n".join(yolo_strings))

In [ ]:
# Convert each annotation to YOLO format and save to .txt file FOR VAL IMAGES
for image_name, image_annotations in val_annotations_dict.items():
    yolo_formatted_annotations = [convert_to_yolo_format(ann, os.path.join(val_images_path, image_name)) for ann in image_annotations]
    yolo_strings = [" ".join(map(str, ann)) for ann in yolo_formatted_annotations]

    txt_path = os.path.join(val_labels_path, image_name.replace('.jpg', '.txt'))

    labels_directory = os.path.dirname(txt_path)
    if not os.path.exists(labels_directory):
      os.makedirs(labels_directory)

    with open(txt_path, 'w') as f:
        f.write("\n".join(yolo_strings))

In [ ]:
#Creating the YAML file
def create_yaml_configuration():
    """
    Creates a .YAML configuration file for training YOLO.
    Returns the path to the created .YAML file.
    """
    # Define the content for the .YAML configuration file
    yaml_content = f"""
    train: /content/data/COCO-Hand/COCO-Hand-Big/train
    test: /content/data/COCO-Hand/COCO-Hand-Big/test
    val: /content/data/COCO-Hand/COCO-Hand-Big/val

    # Classes
    nc: 1
    names: ['hand']
    """

    # Define the path for the .YAML file
    yaml_path = Path('/content/data/COCO-Hand/COCO-Hand-Big/coco_hand_big.yaml')

    # Write the content to the .YAML file
    with open(yaml_path, 'w') as yaml_file:
        yaml_file.write(yaml_content)

    # Return the path to the created .YAML file
    return yaml_path

In [ ]:
#Train model
def train_model(data_yaml):

    model = YOLO("yolov8m.pt")
    model.train(data=data_yaml, epochs=25, project="COCO-Hand", name="COCO_Hand_Big", imgsz=640)
    model.val()

In [ ]:
#Train model using previous weights
def train_model(data_yaml, weights_path=None, additional_epochs=20):
    """
    Train the YOLOv8 model on the COCO Big Hand dataset.
    """

    model = YOLO(weights_path)

    # Continue training the model
    model.train(data=data_yaml, epochs=additional_epochs, project="COCO-Hand", name="COCO_Hand_Big", imgsz=640)
    model.val()



In [ ]:
if __name__ == "__main__":
    data_yaml = create_yaml_configuration()
    previous_weights_path = '/content/drive/Shareddrives/Nikhil shared drive/COCO_Trained model weights yolov8/COCO_Hand_Big/best (1).pt'  # Adjust the path as needed

    # Continue training for additional epochs using the weights from the last checkpoint
    train_model(data_yaml_path, weights_path=previous_weights_path, additional_epochs=20)

Ultralytics YOLOv8.0.203 🚀 Python-3.10.12 torch-2.1.0+cu118 CUDA:0 (Tesla T4, 15102MiB)
engine/trainer: task=detect, mode=train, model=/content/drive/Shareddrives/Nikhil shared drive/COCO_Trained model weights yolov8/COCO_Hand_Big/best (1).pt, data=/content/data/COCO-Hand/COCO-Hand-Big/coco_hand_big.yaml, epochs=20, patience=50, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=COCO-Hand, name=COCO_Hand_Big, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, show=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True, vid_stride=1, stream_buffer=False, line_width=N

In [ ]:
#Uploading weights to drive
def upload_file_to_drive(source_path, destination_path):
    """
    Uploads a file from the Colab environment to Google Drive.

    Parameters:
    - source_path: The path to the file in the Colab environment.
    - destination_path: The path in Google Drive where the file will be stored.
    """
    # Ensure the destination directory exists
    os.makedirs(os.path.dirname(destination_path), exist_ok=True)

    # Copy the file to the destination directory
    shutil.copy(source_path, destination_path)
    print(f"File {source_path} uploaded to {destination_path}")


upload_file_to_drive('/content/COCO-Hand', '/content/drive/Shareddrives/Nikhil shared drive')


In [ ]:
#Testing model starts from here
#Loading the weights
!cp -r "/content/drive/Shareddrives/Nikhil shared drive/COCO_Trained model weights 45 epochs /COCO_Hand_Big/weights/best.pt" "/content"

In [ ]:
#plotting the bounding coordinates on images
def plot_one_box(xyxy, img, label=None, color=None, line_thickness=None):
    """
    Plots one bounding box on an image using OpenCV.

    Args:
    - xyxy (list): List of 4 values representing the bounding box coordinates [x1, y1, x2, y2].
    - img (numpy.ndarray): Image on which to draw the bounding box.
    - label (str, optional): Label to display above the bounding box.
    - color (tuple, optional): Color of the bounding box. Default is red.
    - line_thickness (int, optional): Thickness of the bounding box lines.

    Returns:
    - numpy.ndarray: Image with the bounding box drawn.
    """
    color = color or [0, 0, 255]  # Default color is red
    line_thickness = line_thickness or 2  # Default line thickness is 2
    c1, c2 = (int(xyxy[0]), int(xyxy[1])), (int(xyxy[2]), int(xyxy[3]))
    cv2.rectangle(img, c1, c2, color, thickness=line_thickness)
    if label:
        t_size = cv2.getTextSize(label, 0, fontScale=0.5, thickness=1)[0]
        c2 = c1[0] + t_size[0], c1[1] - t_size[1] - 3
        cv2.rectangle(img, c1, c2, color, -1)  # Negative thickness means filled rectangle
        cv2.putText(img, label, (c1[0], c1[1] - 2), 0, 0.5, [225, 255, 255], thickness=1, lineType=cv2.LINE_AA)
    return img


In [ ]:
#Testing the model
def test_model(weights_path, image_dir, show=False):
    """
    Test the trained YOLOv8 model on a set of images.
    """
    image_dir = Path(image_dir)
    model = YOLO(weights_path)

    for image_path in image_dir.iterdir():
        image = cv2.imread(image_path.as_posix())
        results = model.predict(source=image, conf=0.3, iou=0.4)

        # Extract the bounding boxes
        detections = results[0].boxes.xyxy

        # Attempt to extract confidence scores from the boxes
        try:
            confidences = [box[4].item() for box in detections]
        except IndexError:
            confidences = [1.0] * len(detections)  # Default to confidence of 1.0 if not available

        # Check if there are any detections
        if detections is not None:
            for i, box in enumerate(detections):
                xyxy = box[:4].tolist()
                conf = confidences[i]
                label = f'hand'  # Assuming only 'hand' class
                plot_one_box(xyxy, image, label=label, color=(255, 0, 0), line_thickness=2)

            if show:
                plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
                plt.show()
        else:
            print(f"No results for image {image_path.name}!")


In [ ]:
weights_path = "/content/COCO_Trained model/COCO_Hand_Big/best (1).pt"
test_images_path = "/content/drive/Shareddrives/Nikhil shared drive/hand14k/Images"
test_model(weights_path, test_images_path, show=True)

NameError: ignored

Preprocessing the images, masks by cropping

In [12]:
zip_file_path = '/content/drive/Shareddrives/Nikhil shared drive/GTEA Cropped Dataset 6.6k Images/Cropped_Images.zip'
extraction_path = '/content/data/'

In [13]:
# Unzip the file
with ZipFile(zip_file_path, 'r') as zip_ref:
    zip_ref.extractall(extraction_path)

print("Unzipped successfully!")

Unzipped successfully!


In [10]:
def crop_mask_image(mask_dir, box, original_filename, scale=1.2):
    """
    Crop the mask image using the same bounding box coordinates from the original image.

    Args:
    - mask_dir (str): Directory where the mask images are stored.
    - box (list): List of 4 values representing the bounding box coordinates [x1, y1, x2, y2].
    - original_filename (str): Filename of the original image to find the corresponding mask image.
    - scale (float): Factor to scale the bounding box size.

    Returns:
    - numpy.ndarray: Cropped mask image.
    """
    # Replace the extension of the original filename with .png
    mask_filename = Path(original_filename).stem + '.png'

    # Construct the full path for the mask image
    mask_image_path = Path(mask_dir) / mask_filename
    # Read the mask image
    mask_image = cv2.imread(str(mask_image_path), cv2.IMREAD_UNCHANGED)
    if mask_image is None:
        raise FileNotFoundError(f"The mask image at {mask_image_path} was not found.")

    # Calculate the size of the square bounding box
    x1, y1, x2, y2 = box
    width = x2 - x1
    height = y2 - y1
    side_length = max(width, height) * scale

    # Calculate the center of the original bounding box
    center_x = x1 + width / 2
    center_y = y1 + height / 2

    # Calculate the new bounding box coordinates
    new_x1 = max(int(center_x - side_length / 2), 0)
    new_y1 = max(int(center_y - side_length / 2), 0)
    new_x2 = min(int(center_x + side_length / 2), mask_image.shape[1])
    new_y2 = min(int(center_y + side_length / 2), mask_image.shape[0])

    # Crop the mask image
    cropped_mask = mask_image[new_y1:new_y2, new_x1:new_x2]

    return cropped_mask


In [11]:
def save_cropped_image(image, save_dir, original_filename):
    """
    Save the cropped image to the specified directory with the original filename.

    Args:
    - image (numpy.ndarray): The cropped image to save.
    - save_dir (Path): The directory to save the cropped image.
    - original_filename (str): The original filename for the cropped image.

    Returns:
    - str: The path to the saved image.
    """
    # Create the directory if it doesn't exist
    save_dir.mkdir(parents=True, exist_ok=True)

    # Save the image
    save_path = save_dir / original_filename
    cv2.imwrite(str(save_path), image)

    return str(save_path)


In [19]:
#Cropping the images with (1.2 * s, 1.2 * s) scale
import cv2
from pathlib import Path
import matplotlib.pyplot as plt

def crop_and_resize(image, box, scale=1.2):
    """
    Crop and resize the bounding box in the image.

    Args:
    - image (numpy.ndarray): The image from which to crop.
    - box (list): The bounding box coordinates [x1, y1, x2, y2].
    - scale (float): Factor to scale the bounding box size.

    Returns:
    - numpy.ndarray: The cropped and resized image.
    """
    # Calculate width and height of the box
    width = box[2] - box[0]
    height = box[3] - box[1]
    # Determine the size of the square
    side_length = max(width, height)
    # Calculate the new box coordinates, centered around the original box, with the new size
    center_x, center_y = box[0] + width / 2, box[1] + height / 2
    new_half_size = side_length * scale / 2
    new_x1 = max(center_x - new_half_size, 0)
    new_y1 = max(center_y - new_half_size, 0)
    new_x2 = min(center_x + new_half_size, image.shape[1])
    new_y2 = min(center_y + new_half_size, image.shape[0])
    # Crop the image
    cropped_img = image[int(new_y1):int(new_y2), int(new_x1):int(new_x2)]
    return cropped_img

def test_model(weights_path, image_dir, mask_dir, show=False):
    """
    Test the trained YOLOv8 model on a set of images, crop the hand bounding boxes from both the images and the corresponding masks,
    and save them to separate directories.
    """
    image_dir = Path(image_dir)
    mask_dir = Path(mask_dir)
    cropped_images_dir = Path('Cropped_Images')
    cropped_masks_dir = Path('Cropped_Masks')
    model = YOLO(weights_path)
    hand_detection_count = 0

    for image_path in image_dir.iterdir():
        image = cv2.imread(str(image_path))
        results = model.predict(source=image, conf=0.3, iou=0.4)

        # Extract the bounding boxes
        detections = results[0].boxes.xyxy

        # Check if there are any detections
        if detections is not None and len(detections) > 0:
            hand_detection_count += 1  # Increment the counter for each image with a detection
            for i, box in enumerate(detections):
                xyxy = box[:4].tolist()
                cropped_image = crop_and_resize(image, xyxy)
                cropped_mask = crop_mask_image(mask_dir, xyxy, image_path.name)

                # Save the cropped image and mask
                cropped_image_path = save_cropped_image(cropped_image, cropped_images_dir, image_path.name)
                cropped_mask_path = save_cropped_image(cropped_mask, cropped_masks_dir, image_path.name)

                '''if show:
                    # Show the cropped image and mask side by side
                    fig, axs = plt.subplots(1, 2, figsize=(10, 5))
                    axs[0].imshow(cv2.cvtColor(cropped_image, cv2.COLOR_BGR2RGB))
                    axs[0].set_title('Cropped Image')
                    axs[1].imshow(cropped_mask, cmap='gray')
                    axs[1].set_title('Cropped Mask')
                    plt.show()'''

        else:
            print(f"No results for image {image_path.name}")
    print(f"Total number of images with detected hands: {hand_detection_count}")




In [ ]:
weights_path = "/content/drive/Shareddrives/Nikhil shared drive/COCO_Hand_Big2/weights/best.pt"
test_images_path = "/content/data/Images"
mask_dir="/content/data/Masks"
test_model(weights_path, test_images_path,mask_dir, show=True)


0: 480x640 (no detections), 120.0ms
Speed: 20.2ms preprocess, 120.0ms inference, 31.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 28.0ms
Speed: 2.4ms preprocess, 28.0ms inference, 26.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 28.2ms
Speed: 3.7ms preprocess, 28.2ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)



No results for image P21-R06-GreekSalad_000121.jpg


0: 480x640 1 hand, 28.0ms
Speed: 4.1ms preprocess, 28.0ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 28.1ms
Speed: 3.5ms preprocess, 28.1ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 28.3ms
Speed: 3.6ms preprocess, 28.3ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 28.0ms
Speed: 3.7ms preprocess, 28.0ms inference, 1.4ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 28.2ms
Speed: 3.9ms preprocess, 28.2ms inference, 1.2ms postprocess per image at shape (1, 3, 480, 640)



No results for image P03-R01-PastaSalad_000189.jpg


0: 480x640 1 hand, 24.4ms
Speed: 3.8ms preprocess, 24.4ms inference, 2.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 22.9ms
Speed: 3.7ms preprocess, 22.9ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 22.7ms
Speed: 3.9ms preprocess, 22.7ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 hands, 22.8ms
Speed: 2.6ms preprocess, 22.8ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 21.4ms
Speed: 2.7ms preprocess, 21.4ms inference, 0.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 19.1ms
Speed: 3.7ms preprocess, 19.1ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)



...

No results for image P25-R06-GreekSalad_000362.jpg
No results for image P12-R02-TurkeySandwich_000017.jpg
No results for image OP03-R05-Cheeseburger_000136.jpg
No results for image P13-R01-PastaSalad_000116.jpg
No results for image OP06-R06-GreekSalad_000045.jpg


0: 480x640 1 hand, 19.3ms
Speed: 3.6ms preprocess, 19.3ms inference, 1.5ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 18.5ms
Speed: 4.7ms preprocess, 18.5ms inference, 1.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 18.5ms
Speed: 2.9ms preprocess, 18.5ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 18.5ms
Speed: 3.0ms preprocess, 18.5ms inference, 0.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 18.5ms
Speed: 3.0ms preprocess, 18.5ms inference, 1.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 18.5ms
Speed: 3.0ms preprocess, 18.5ms inference, 0.9ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 18.5ms
Speed: 3.2ms preprocess, 18.5ms inference, 0.8ms postprocess per image at shape (1, 3, 480, 640)


No results for image P23-R03-BaconAndEggs_000136.jpg
No results for image P10-R01-PastaSalad_000219.jpg
No results for image OP06-R02-TurkeySandwich_000052.jpg
No results for image P21-R04-ContinentalBreakfast_000040.jpg



0: 480x640 1 hand, 18.5ms
Speed: 3.1ms preprocess, 18.5ms inference, 1.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 hand, 18.6ms
Speed: 3.0ms preprocess, 18.6ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)


Total number of images with detected hands: 6623


In [22]:
def smooth_mask(mask, blur_size=3):
    """
    Apply Gaussian blur to the mask to smooth the edges.

    Args:
    - mask (numpy.ndarray): The mask image.
    - blur_size (int): Size of the kernel to use for the Gaussian blur.

    Returns:
    - numpy.ndarray: The smoothed mask.
    """
    return cv2.GaussianBlur(mask, (blur_size, blur_size), 0)


In [23]:
#To convert the masked images into labels txt file
import cv2
import numpy as np
from pathlib import Path

def mask_to_polygons(mask):
    """
    Convert a mask image to a list of polygons.

    Args:
    - mask (numpy.ndarray): The mask image.

    Returns:
    - list: A list of polygons, each represented as a list of points (x, y).
    """
    # Find contours in the mask
    contours, _ = cv2.findContours(mask, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
    polygons = []
    for contour in contours:
        # Approximate the contour to a polygon
        epsilon = 0.005 * cv2.arcLength(contour, True)
        approx = cv2.approxPolyDP(contour, epsilon, True)
        polygon = approx.ravel().tolist()
        # Skip small or invalid contours
        if len(polygon) >= 6:
            polygons.append(polygon)
    return polygons





In [24]:
def save_polygons_to_txt(polygons, save_path):
    """
    Save the polygon coordinates to a .txt file.

    Args:
    - polygons (list): A list of polygons.
    - save_path (Path): The path to the .txt file where the coordinates will be saved.
    """
    with open(save_path, 'w') as file:
        for polygon in polygons:
            coordinates = ','.join(map(str, polygon))
            file.write(coordinates + '\n')

In [25]:
#Converting masks into labels
def process_masks_to_polygons(masks_dir, labels_dir):
    """
    Process all mask images in a directory, convert them to polygons, and save the results to .txt files.

    Args:
    - masks_dir (str): Directory where the mask images are stored.
    - labels_dir (str): Directory where the .txt files will be saved.
    """
    masks_dir = Path(masks_dir)
    labels_dir = Path(labels_dir)
    labels_dir.mkdir(parents=True, exist_ok=True)

    for mask_path in masks_dir.glob('*.jpg'):
        mask = cv2.imread(str(mask_path), cv2.IMREAD_GRAYSCALE)
        if mask is None:
            continue
        mask = smooth_mask(mask)
        polygons = mask_to_polygons(mask)
        txt_filename = mask_path.stem + '.txt'
        save_path = labels_dir / txt_filename
        save_polygons_to_txt(polygons, save_path)

masks_dir = '/content/data/Cropped_Masks'
labels_dir = '/content/data/Cropped_Labels'
process_masks_to_polygons(masks_dir, labels_dir)


In [26]:
#Plotting the LABELS on Images and placing in folder
import cv2
import numpy as np
import matplotlib.pyplot as plt
import os

# Function to read polygons from a text file
def read_polygons_from_file(file_path):
    polygons = []
    with open(file_path, 'r') as file:
        for line in file:
            points = line.strip().split(',')
            polygon = list(zip(map(int, points[::2]), map(int, points[1::2])))
            polygons.append(polygon)
    return polygons

# Paths to the folders containing images and labels
images_folder_path = '/content/drive/Shareddrives/Nikhil shared drive/GTEA Cropped Dataset 6.6k Images/Cropped_Images'  # Replace with your images folder path
labels_folder_path = '/content/data/Cropped_Labels'  # Replace with your labels folder path
output_folder_path = '/content/data/Cropped_LabelsonImages'

# Create the output folder if it doesn't exist
if not os.path.exists(output_folder_path):
    os.makedirs(output_folder_path)

# Get a list of image files and corresponding label files
image_files = [f for f in os.listdir(images_folder_path) if f.endswith('.jpg')]
label_files = [f.replace('.jpg', '.txt') for f in image_files]

# Loop through the image and label files
for image_file, label_file in zip(image_files, label_files):
    image_path = os.path.join(images_folder_path, image_file)
    label_path = os.path.join(labels_folder_path, label_file)
    output_image_path = os.path.join(output_folder_path, image_file)
    # Read polygons from the text file
    polygons = read_polygons_from_file(label_path)

    # Load the image
    image = cv2.imread(image_path)

    # Check if the image was successfully loaded
    if image is None:
        print(f"Error: Image {image_file} not found.")
        continue

    # Convert image to RGB (OpenCV uses BGR by default)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # Draw the polygons on the image
    for polygon in polygons:
        pts = np.array(polygon, np.int32)
        pts = pts.reshape((-1, 1, 2))
        cv2.polylines(image, [pts], isClosed=True, color=(0, 255, 0), thickness=2)

    # Save the image with polygons
    cv2.imwrite(output_image_path, cv2.cvtColor(image, cv2.COLOR_RGB2BGR))

print("Processing complete. Images with labeled polygons are saved in 'Cropped_LabelsonImages' folder.")

'''# Display the image with polygons
    plt.imshow(image)
    plt.title(f'Polygons on {image_file}')
    plt.axis('off')  # Hide the axis
    plt.show()'''


Processing complete. Images with labeled polygons are saved in 'Cropped_LabelsonImages' folder.


"# Display the image with polygons\n    plt.imshow(image)\n    plt.title(f'Polygons on {image_file}')\n    plt.axis('off')  # Hide the axis\n    plt.show()"

In [28]:
#To download folder into local system
import os
from google.colab import files
from zipfile import ZipFile

def zip_folder(folder_path, zip_path):
    """
    Zip the contents of an entire folder (with that folder included in the archive).
    Existing files with the same name will be overwritten.

    Args:
    - folder_path (str): The path to the folder to zip.
    - zip_path (str): The complete target path for the created zip file.
    """
    with ZipFile(zip_path, 'w') as zipf:
        for root, dirs, files in os.walk(folder_path):
            for file in files:
                # Create a relative path for files to keep the directory structure
                relative_path = os.path.relpath(os.path.join(root, file), os.path.join(folder_path, '..'))
                zipf.write(os.path.join(root, file), relative_path)

def download_folder(folder_path):
    """
    Compress and download the given folder.

    Args:
    - folder_path (str): The path to the folder to download.
    """
    zip_path = f"{folder_path}.zip"
    zip_folder(folder_path, zip_path)
    files.download(zip_path)

# Example usage:
folder_to_download = '/content/data/Cropped_Labels'  # Change this to the path of the folder you want to download
download_folder(folder_to_download)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [27]:
#to count number of images in a directory
import os

def count_images_in_folder(folder_path):
    # List all files in the folder
    files = os.listdir(folder_path)
    # Count files with image extensions (assuming common image formats)
    image_count = sum(1 for file in files if file.lower().endswith(('.png', '.jpg', '.jpeg', '.txt', '.gif', '.tiff')))
    return image_count

folder_path = '/content/data/Cropped_LabelsonImages'  # Replace with your folder path
print(f"Number of images in the folder: {count_images_in_folder(folder_path)}")


Number of images in the folder: 6623


In [ ]:
#renaming files in folder
import os

# Define the directory where your images are located
directory = "/content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks"  # Adjust the path to your specific directory

# Iterate over all files in the directory
for filename in os.listdir(directory):
    if filename.startswith("Mask_"):  # Check if the filename starts with "Image_"
        # Construct the old file path
        old_file = os.path.join(directory, filename)

        # Construct the new file path with "Image_" removed from the filename
        new_file = os.path.join(directory, filename.replace("Mask_", ""))

        # Rename the file
        os.rename(old_file, new_file)
        print(f'Renamed: {old_file} to {new_file}')


Streaming output truncated to the last 5000 lines.
Renamed: /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/Mask_OP04-R03-BaconAndEggs_018971.jpg to /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/OP04-R03-BaconAndEggs_018971.jpg
Renamed: /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/Mask_P03-R01-PastaSalad_000164.jpg to /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/P03-R01-PastaSalad_000164.jpg
Renamed: /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/Mask_P20-R03-BaconAndEggs_000145.jpg to /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/P20-R03-BaconAndEggs_000145.jpg
Renamed: /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/Mask_P07-R01-PastaSalad_000466.jpg to /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/P07-R01-PastaSalad_000466.jpg
Renamed: /content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks/Mask_OP02-R07-Pizza_000058.jpg to /content/drive/Shareddrives/Ni

In [ ]:
#To clear entire directory contents
import shutil
import os

def clear_directory_contents(dir_path):
    """
    Remove all files and subdirectories in the specified directory.

    Args:
    - dir_path (str): The path to the directory to clear.
    """
    for filename in os.listdir(dir_path):
        file_path = os.path.join(dir_path, filename)
        try:
            if os.path.isfile(file_path) or os.path.islink(file_path):
                os.unlink(file_path)
            elif os.path.isdir(file_path):
                shutil.rmtree(file_path)
        except Exception as e:
            print(f'Failed to delete {file_path}. Reason: {e}')

# Example usage:
directory_to_clear = '/content/drive/Shareddrives/Nikhil shared drive/Cropped_Masks'  # Replace with your directory path
clear_directory_contents(directory_to_clear)


In [ ]:
#To upload folder from colab to drive
import shutil
from pathlib import Path

def upload_file_to_drive(source, destination):
    source_path = Path(source)
    destination_path = Path(destination)

    # Check if the source is a file or directory
    if source_path.is_file():
        # Copy the file
        shutil.copy2(source, destination)
    elif source_path.is_dir():
        # Copy the directory
        destination_path = destination_path / source_path.name
        shutil.copytree(source, destination_path)
    else:
        print(f"The source {source} is neither a file nor a directory.")


upload_file_to_drive('/content/Cropped_LabelsonImages', '/content/drive/MyDrive')